In [1]:
from IPython.display import Markdown as md
from IPython.display import display, HTML
import pandas as pd
import numpy as np
import ipywidgets as widgets
from pathlib import Path
from datetime import datetime
from recopytex import flat_df_students, pp_q_scores
from datetime import datetime


import chart_studio.plotly as py
import plotly.graph_objects as go
import plotly.figure_factory as ff

from plotly.offline import iplot, init_notebook_mode
init_notebook_mode()

In [2]:
tribe = "ES"
assessment = "ds2"
date = "14/10/19"
csv_file = Path(f"../{tribe}/191014_{assessment}.csv")

In [3]:
# Parameters
tribe = "2gt1"
assessment = "Ds3"
date = "18/01/23"
csv_file = "/home/lafrite/Cours/2022-2023/Notes/2gt1/230118_DS3.csv"


In [4]:
date = datetime.strptime(date, "%d/%m/%y")
output_path = Path(csv_file[:-4])
print(output_path)

/home/lafrite/Cours/2022-2023/Notes/2gt1/230118_DS3


In [5]:
if date is None:
    display(md(f"# {assessment} pour {tribe}"))
else:
    display(md(f"# {assessment} ({date:%y/%m/%d}) pour {tribe}"))

# Ds3 (23/01/18) pour 2gt1

In [6]:
stack_scores = pd.read_csv(csv_file, encoding="UTF8")
#comments = stack_scores.iloc[0]
#stack_scores.drop([0], inplace=True)
scores = flat_df_students(stack_scores).dropna(subset=["Score"])
scores = pp_q_scores(scores)
#scores.head()
#comments.drop()

In [7]:
exercises_scores = scores.groupby(["Exercice", "Eleve"]).agg({"Note": "sum", "Bareme": "sum"})

In [8]:
exercises_scores.head()

Note  Bareme
Exercice   Eleve                          
Exercice 1 ACHOUR Ilyes       4.50     7.0
           BELARBI Islem      2.83     7.0
           BEN ELALLID Hajar  1.67     7.0
           BISWAS Lina        3.84     7.0
           BOULAABA Rayan     5.01     7.0

In [9]:
assessment_scores = scores.groupby(["Eleve"]).agg({"Note": "sum", "Bareme": "sum"})

In [10]:
scores.columns

Index(['Nom', 'Trimestre', 'Date', 'Exercice', 'Question', 'Competence',
       'Domaine', 'Commentaire', 'Est_nivele', 'Bareme', 'Eleve', 'Score',
       'Note', 'Niveau', 'Normalise'],
      dtype='object')

In [11]:
domain_scores = scores.groupby(["Eleve", "Domaine"]).agg({"Note": "sum", "Bareme": "sum"})
domain_scores["Normalized"] = domain_scores["Note"] / domain_scores["Bareme"]

In [12]:
#domain_scores

In [13]:
competence_scores = scores.groupby(["Eleve", "Competence"]).agg({"Note": "sum", "Bareme": "sum"})
competence_scores["Normalized"] = competence_scores["Note"] / competence_scores["Bareme"]

In [14]:
competence_scores.tail()

Note  Bareme  Normalized
Eleve           Competence                           
TROPHARDY Eline Chercher     3.67     4.0        0.92
                Communiquer  1.00     1.0        1.00
                Modéliser    1.00     1.0        1.00
                Rechercher   1.50     1.5        1.00
                Représenter  6.00     6.5        0.92

### Bilans personnalisés

In [15]:
import pytex
#scores.head()

In [16]:
datas = {
    "assessment": {
        "name": assessment,
        "date": date
    },
    #"exercises": scores["Exercice"].unique(),
    #"questions": scores[["Exercice", 'Question', 'Competence', 'Domaine', 'Commentaire', 'Bareme', 'Est_nivele']],
    "eleves": {}
}
for e in scores["Eleve"].unique():
    edatas =  {
        "e": e,
        "assessment": assessment_scores.loc[e],
        "exercices": exercises_scores.xs(e, level="Eleve"),        "exercices": exercises_scores.xs(e, level="Eleve"),
        "domains": domain_scores.xs(e, level="Eleve"),
        "competences": competence_scores.xs(e, level="Eleve"),
        "exscores": {}
    }
    for i, ex in edatas["exercices"].iterrows():
        edatas["exscores"][i] = scores.loc[(scores.Exercice==i) & (scores.Eleve==e)]
    datas["eleves"][e] = edatas

In [17]:
score_template = r"""
\documentclass[a5paper,10pt]{article}
\usepackage{fullpage}
\usepackage{booktabs}
\usepackage{longtable}
\usepackage{tikz}
\usepackage{multicol}

\usepackage{geometry}
\geometry{left=10mm,right=10mm, top=10mm}

\renewcommand{\arraystretch}{1}
\setlength{\columnseprule}{0pt}

\pagestyle{empty}


\begin{document}


    \section*{\Var{assessment.name} \hfill \Var{e} \hfill \Var{sc.assessment.Note}/\Var{sc.assessment.Bareme}}
    %- for i,ex in sc.exercices.iterrows() 
        \subsection*{\Var{i}: \hfill \Var{ex.Note} / \Var{ex.Bareme}}
        \begin{center}
        \Var{sc.exscores[i].to_latex(index=False, columns=["Question", "Domaine", "Commentaire", "Note", "Bareme"])}
        \end{center}
    %- endfor
 
     \subsection*{Compétences}
     \begin{multicols}{2}
    %- for i,dom in sc.competences.iterrows()
        \noindent
        \Var{i} \hfill
        \begin{tikzpicture}[scale=0.7]
            \draw [](0,0) rectangle (3, 1);
            \draw [fill=black!20] (0, 0) rectangle (\Var{dom.Normalized*3}, 1);
        \end{tikzpicture}
        \hfill
        %\Var{dom.Normalized}
        
    %- endfor
    \end{multicols}

\end{document}
"""

In [18]:
tpl = pytex.texenv.from_string(score_template)

for e,sc in datas['eleves'].items():
    reportfilename = f"{date:%y%m%d}_{assessment}_{e}.tex"
    with open(output_path / reportfilename, "w") as f:
        f.write(tpl.render(sc=sc, e=e,**datas))
    print(f"Wrote {reportfilename}")
    pytex.pdflatex(reportfilename)

Wrote 230118_Ds3_ACHOUR Ilyes.tex
Wrote 230118_Ds3_BELARBI Islem.tex
Wrote 230118_Ds3_BEN ELALLID Hajar.tex
Wrote 230118_Ds3_BISWAS Lina.tex
Wrote 230118_Ds3_BOULAABA Rayan.tex
Wrote 230118_Ds3_BREZUN Ines.tex
Wrote 230118_Ds3_BUGNON Enzo.tex
Wrote 230118_Ds3_CALLEWAERT Idaline.tex
Wrote 230118_Ds3_CATTIN Clément.tex
Wrote 230118_Ds3_CHRISTMANN Nathan.tex
Wrote 230118_Ds3_DECOSTER Clément.tex
Wrote 230118_Ds3_DEHIMAT Launy.tex
Wrote 230118_Ds3_DUPONT Jessica.tex
Wrote 230118_Ds3_GASAN Jéssica.tex
Wrote 230118_Ds3_GEORGET Raphaël.tex
Wrote 230118_Ds3_HABBAZ Hajar.tex
Wrote 230118_Ds3_JACQUEMIER Samuel.tex
Wrote 230118_Ds3_JACQUIER Juliette.tex
Wrote 230118_Ds3_JOVIC Atanase.tex
Wrote 230118_Ds3_KASSI Cheïma.tex
Wrote 230118_Ds3_KICHENASSAMY Sanjay.tex
Wrote 230118_Ds3_LE VEUZIT Adrien.tex
Wrote 230118_Ds3_LETIF Ilef.tex
Wrote 230118_Ds3_MANJALI Hiba.tex
Wrote 230118_Ds3_NEIVA Hugo.tex
Wrote 230118_Ds3_OLLIET Gioia.tex
Wrote 230118_Ds3_PERNOT Gabin.tex
Wrote 230118_Ds3_RIZZI Elisa.tex
Wr

## Envoie des bilans par mail

In [19]:
mailfrom = "benjamin.bertrand@ac-lyon.fr"
subject = f"Bian du devoir {assessment}"
message = """Bonsoir,
En pièce jointe, vous trouverez un document détaillant la note du devoir.
B.Bertrand
"""
print(subject)
print(message)

Bian du devoir Ds3
Bonsoir,
En pièce jointe, vous trouverez un document détaillant la note du devoir.
B.Bertrand



In [20]:
import smtplib
import os
import sys
from email.message import EmailMessage
import mimetypes
import time
import random

In [21]:
def build_msg(subj, to_addr, from_addr, body, att):
    msg = EmailMessage()
    msg["Subject"] = subj
    msg["To"] = to_addr
    #msg["To"] = "lafrite26@gmail.com"
    msg["From"] = from_addr
    msg.set_content(body)

    if att != []:
        ctype, encoding = mimetypes.guess_type(att)
        if ctype is None or encoding is not None:
            ctype = 'application/octet-stream'
        maintype, subtype = ctype.split('/', 1)
        with open(att, "rb") as f:
            msg.add_attachment(f.read(),
                maintype=maintype,
                subtype=subtype,
                filename=att.name)
    return msg


In [26]:
send = 1
fake = 0

In [27]:
if send:
    if fake:
        server = smtplib.SMTP("localhost", 8025)
        server.ehlo()
    else:
        server = smtplib.SMTP("smtps.ac-lyon.fr", 587)
        server.ehlo()
        server.starttls()
        server.ehlo()
        server.login("bbertrand", os.popen("pass Prof/Lyon/bbertrand").read()[:-1])   

In [28]:
try:
    eleves_data = pd.read_csv(f"../../{tribe}.csv")
except FileNotFoundError:
    try:
        eleves_data = pd.read_csv(f"../{tribe}.csv")
    except FileNotFoundError:
        eleves_data = pd.read_csv(f"{tribe}.csv")
eleves_data.fillna("", inplace=True)
#eleves_data

In [29]:
for e in eleves_data.iterrows():
    reportfilename = Path(f"{date:%y%m%d}_{assessment}_{e[1]['Nom']}.pdf")
    try:
        assert reportfilename.exists()
    except:
        print(f"Pas de rapport pour {e[1]['Nom']}")
    else:
        if e[1]["mail"] != "":
            if send:
                msg = build_msg(subject, e[1]["mail"], mailfrom, message, reportfilename)
                server.send_message(msg)
                print(f"\tBilan envoyé à {e[1]['Nom']}")
        else:
            print(f"Pas de mail pour {e[1]['Nom']}")
            

	Bilan envoyé à ACHOUR Ilyes
	Bilan envoyé à BELARBI Islem
	Bilan envoyé à BEN ELALLID Hajar
	Bilan envoyé à BISWAS Lina
	Bilan envoyé à BOULAABA Rayan
	Bilan envoyé à BREZUN Ines
	Bilan envoyé à BUGNON Enzo
	Bilan envoyé à CALLEWAERT Idaline
	Bilan envoyé à CATTIN Clément
	Bilan envoyé à CHRISTMANN Nathan
	Bilan envoyé à DECOSTER Clément
	Bilan envoyé à DEHIMAT Launy
	Bilan envoyé à DUPONT Jessica
	Bilan envoyé à GASAN Jéssica
	Bilan envoyé à GEORGET Raphaël
	Bilan envoyé à HABBAZ Hajar
	Bilan envoyé à JACQUEMIER Samuel
	Bilan envoyé à JACQUIER Juliette
	Bilan envoyé à JOVIC Atanase
	Bilan envoyé à KASSI Cheïma
	Bilan envoyé à KICHENASSAMY Sanjay
	Bilan envoyé à LE VEUZIT Adrien
	Bilan envoyé à LETIF Ilef
	Bilan envoyé à MANJALI Hiba
Pas de rapport pour MUTTONI Lou
	Bilan envoyé à NEIVA Hugo
	Bilan envoyé à OLLIET Gioia
	Bilan envoyé à PERNOT Gabin
	Bilan envoyé à RIZZI Elisa
	Bilan envoyé à ROSTANT Emma
	Bilan envoyé à SIBABA Moaad
	Bilan envoyé à SOUJOL Damien
	Bilan envoyé à THORAL